In [22]:
import spacy
import pandas as pd
from spacy import displacy
file=pd.read_csv('/content/drive/MyDrive/machine_learning /archive (4)/mtsamples.csv')
file.head()

Unnamed: 0  ...                                           keywords
0           0  ...  allergy / immunology, allergic rhinitis, aller...
1           1  ...  bariatrics, laparoscopic gastric bypass, weigh...
2           2  ...  bariatrics, laparoscopic gastric bypass, heart...
3           3  ...  cardiovascular / pulmonary, 2-d m-mode, dopple...
4           4  ...  cardiovascular / pulmonary, 2-d, doppler, echo...

[5 rows x 6 columns]

In [6]:
surgery = set(['acute cholangitis', 'appendectomy',
               'appendicitis', 'cholecystectomy',
               'laser capsulotomy', 'surgisis xenograft',
               'sclerotomies', 'tonsillectomy'
               ])

In [8]:
nlp=spacy.load('en_core_web_sm')
print(nlp)

In [14]:
def perform_ner(text):
  document=nlp(text)
  entity=[(ent.text,ent.label) for ent in document.ents]
  displacy.render(document,style="ent",jupyter=True)
  return entity

file['ner_results'] =file['description'].apply(perform_ner)

/usr/local/lib/python3.10/dist-packages/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


In [21]:
for index , row in file.head(20).iterrows():
  print(f"TEXT:{row['description']}\nNER RESULTS:{row['ner_results']}")

TEXT: A 23-year-old white female presents with complaint of allergies.
NER RESULTS:[('23-year-old', 391)]
TEXT: Consult for laparoscopic gastric bypass.
NER RESULTS:[]
TEXT: Consult for laparoscopic gastric bypass.
NER RESULTS:[]
TEXT: 2-D M-Mode. Doppler.  
NER RESULTS:[('2', 397)]
TEXT: 2-D Echocardiogram
NER RESULTS:[]
TEXT: Morbid obesity.  Laparoscopic antecolic antegastric Roux-en-Y gastric bypass with EEA anastomosis.  This is a 30-year-old female, who has been overweight for many years.  She has tried many different diets, but is unsuccessful. 
NER RESULTS:[('Morbid', 380), ('EEA', 383), ('30-year-old', 391), ('many years', 391)]
TEXT: Liposuction of the supraumbilical abdomen, revision of right breast reconstruction, excision of soft tissue fullness of the lateral abdomen and flank.

NER RESULTS:[]
TEXT: 2-D Echocardiogram
NER RESULTS:[]
TEXT: Suction-assisted lipectomy - lipodystrophy of the abdomen and thighs.
NER RESULTS:[]
TEXT: Echocardiogram and Doppler
NER RESULTS:[]
TE

In [23]:
import spacy
from spacy.lang.en import English
from spacy.pipeline import EntityRuler
class RulerModel():
    def __init__(self, surgery, internalMedicine, medication, obstetricsGynecology):
        self.ruler_model = spacy.blank('en')
        self.entity_ruler =      self.ruler_model.add_pipe('entity_ruler')

        total_patterns = []
        patterns = self.create_patterns(surgery, 'surgery')
        total_patterns.extend(patterns)
        patterns = self.create_patterns(internalMedicine, 'internalMedicine')
        total_patterns.extend(patterns)
        patterns = self.create_patterns(medication, 'medication')
        total_patterns.extend(patterns)

        patterns = self.create_patterns(obstetricsGynecology, 'obstetricsGynecology')
        total_patterns.extend(patterns)

        self.add_patterns_into_ruler(total_patterns)

        self.save_ruler_model()

    def create_patterns(self, entity_type_set, entity_type):
        patterns = []
        for item in entity_type_set:
            pattern = {'label': entity_type, 'pattern': item}
            patterns.append(pattern)
        return patterns

    def add_patterns_into_ruler(self, total_patterns):
        self.entity_ruler.add_patterns(total_patterns)